# Using the CMR API and asyncio for fast CMR Queries  

---

## Summary  

This tutorial demonstrates how to effectively perform queries and extract data download Uniform Resource Locators (URLs) for every Common Metadata Repository (CMR) metadata record within a NASA Earthdata collection. Two examples are shown. The first highlight making sequential requests for data URLs associated with specified collections. The second example demonstrates the how to leverages Python's `asyncio` package to perform bulk parallel requests for the same information and highlights the increase in speed when doing so. The NASA Earthdata collections highlighted here are Harmonized Landsat Sentinel-2 Operational Land Imager Surface Refleactance and TOA Brightness Daily Global 30m ([HLSL30.002](https://doi.org/10.5067/HLS/HLSL30.002)) and
Harmonized Landsat Sentinel-2 Multi-spectral Instrument Surface Reflactance Daily Global 30m ([HLSS30.002](https://doi.org/10.5067/HLS/HLSS30.002)).  

### What is CMR?  

The CMR is a metadata system that catalogs NASA's Earth Observing System Data and Information System (EOSDIS) data and associated metadata. The CMR Application Programming Interface (API) provides programatic search capabilities through CMR's vast metadata holdings using various parameters and keywords. When querying NASA's CMR, there is a limit of 1 million granule matched with only 2000 granules returned per page. This guide shows how to search for CMR records using the CMR API and create a list of download URLs. This guide also shows how to leverage asynchronous, or parallel requests, to increase the speed of this process. The example below leverages the Harmonized Landsat Sentinel-2 collection archived by NASA's LP DAAC to demonstrate how to use Python's `asyncio` to perform large queries again NASA's CMR.  

## Objectives  

+ Use the CMR API and Python to perform large queries (requests that return more than 2000 granules) against NASA's CMR.  
+ Prepare a list of URLs to access or download assets associated with those granules.  
+ Utilize asynchronous/parallel requests to increase speed of query and list construction.  

---

## Getting Started  

Import the required packages.


In [3]:
import requests
import math
import aiohttp
import asyncio
import time
import earthaccess

auth = earthaccess.login(persist=True)

/Users/lshms102/miniconda3/envs/MPCP_lassasentinel/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Searching the CMR

Set the CMR API Endpoint. This is the URL that we'll use to search through the CMR.

In [4]:
CMR_OPS = 'https://cmr.earthdata.nasa.gov/search' # CMR API Endpoint
url = f'{CMR_OPS}/{"granules"}'

To search the CMR we need to set our parameters. In this example we'll narrow our search using Collection IDs, a range of dates and times, and the number of results we want to show per page. Spatial areas can also be used to narrow searches (example shown in [HLS_Tutorial](https://git.earthdata.nasa.gov/projects/LPDUR/repos/hls-tutorial/browse/HLS_Tutorial.ipynb)). 

Here, we are interested in both HLS Landsat-8 and Sentinel-2 collections collected from October 17-19, 2021. Specify the `collections` to search, set a `datetime_range` and set the quantity of results to return per page using the `page_size` parameter like below.  

In [5]:
collections = ['C1748058432-LPCLOUD'] # Collection or concept_id specific to LPDAAC Products (HLS Landsat OLI and HLS Sentinel-2 respectively) 
datetime_range = '2000-02-24T00:00:00Z,2025-07-08T00:00:00Z'
page_size = 2000
has_opendap_url = True

A CMR search can find up to 1 million items or granules, but the number returned per page is limited to 2000, meaning large searches may have several pages of results. By default, `page_size` is set to 10.

## Submitting Requests

Using the above search criteria we can make a request using the `requests.get()` function. Submit a request and print the `response.status_code`.


In [6]:
response = requests.get(url, 
                        params={
                            'concept_id': collections,
                            'temporal': datetime_range,
                            'page_size': page_size
                            },
                        headers={
                            'Accept': 'application/json'
                            }
                       )
print(response.status_code)

200


A status code of 200 indicates the request has succeeded. 

To see the number of results, print the `CMR-Hits` found in the returned header.

In [7]:
print(response.headers['CMR-Hits']) # Resulting quantity of granules/items.

2906771


## Building a List of File URLs

We can build a list of URLs to data assets using our search results. Notice this only uses the first page of results.

In [8]:
granules = response.json()['feed']['entry']
len(granules) # Resulting quantity of granules on page one.

2000

In [10]:
granules

[{'producer_granule_id': 'MOD11A1.A2000055.h12v10.061.2020043121102',
  'time_start': '2000-02-24T00:00:00.000Z',
  'cloud_cover': '100.0',
  'updated': '2020-03-12T13:34:27.235Z',
  'dataset_id': 'MODIS/Terra Land Surface Temperature/Emissivity Daily L3 Global 1km SIN Grid V061',
  'data_center': 'LPCLOUD',
  'title': 'MOD11A1.A2000055.h12v10.061.2020043121102',
  'coordinate_system': 'GEODETIC',
  'day_night_flag': 'BOTH',
  'time_end': '2000-02-24T23:59:59.000Z',
  'id': 'G2182409129-LPCLOUD',
  'original_format': 'ECHO10',
  'granule_size': '0.16838',
  'browse_flag': True,
  'polygons': [['-19.9958333 -63.8551033 -19.9958333 -53.2133438 -10.0041667 -50.7768725 -10.0041667 -60.9313825 -19.9958333 -63.8551033']],
  'collection_concept_id': 'C1748058432-LPCLOUD',
  'online_access_flag': True,
  'links': [{'rel': 'http://esipfed.org/ns/fedsearch/1.1/data#',
    'title': 'Download MOD11A1.A2000055.h12v10.061.2020043121102.hdf',
    'hreflang': 'en-US',
    'href': 'https://data.lpdaac.

In [9]:
file_list = []
for g in granules:
    file_list.extend([x['href'] for x in g['links'] if 'https' in x['href'] and '.hdf' in x['href']])
len(file_list) # Total number of assets from page one of granules.

2000

Print part of the URLs list. 

In [ ]:
file_list[:25]

This process can be extended to all pages of search results to build a complete list of asset URLs. 

## Creating a List from Multiple Results Pages

To create a list from multiple results pages, we first define a function to build a list of pages based upon the number of results.

In [ ]:
def get_page_total(collections, datetime_range, page_size):
    hits = requests.get(url, 
                        params={
                            'concept_id': collections,
                            'temporal': datetime_range,
                            'page_size': page_size,
                            },
                        headers={
                            'Accept': 'application/json'
                            }
                       ).headers['CMR-Hits']
    return math.ceil(int(hits)/page_size)

Then we build a list of pages called `page_numbers`.

In [ ]:
page_numbers = list(range(1, get_page_total(collections, datetime_range, page_size)+1))
page_numbers

After we have a list of pages we can iterate through page by page to make a complete list of assets matching our search.

In [ ]:
data_urls = [] # empty list
start = time.time() # Begin timer
for n in page_numbers: # Iterate through requests page by page sequentially
    print(f'Page: {n}') # Print Page Number
    response = requests.get(url, # Same request function as used previously
                            params={
                                'concept_id': collections,
                                'temporal': datetime_range,
                                'page_size': page_size,
                                'page_num': n
                            },
                            headers={
                                'Accept': 'application/json'
                            }
                           )
    print(f'Page {n} Resonse Code: {response.status_code}') # Show the response code for each page
    
    granules = response.json()['feed']['entry']
    print(f'Number of Granules: {len(granules)}') # Show the number of granules on each page
    
    for g in granules:
        data_urls.extend([x['href'] for x in g['links'] if 'https' in x['href'] and '.hdf' in x['href']])
end = time.time()
print(f'Total time: {end-start}') # Record the total time taken

Show the total quantity of assets in our list matching search parameters.

In [ ]:
len(data_urls)

We can also see that the first 25 assets match up from our first page only search results.

In [ ]:
file_list[:25]==data_urls[:25]



## Improve speed using Asynchronous Requests

You may have noticed the total time the function above took to run. For searches with a large quantity of results, we can query and build a list of asset URLs more quickly by utilizing asynchronous requests. Asynchronous requests can be run concurrently or in parallel, which typically decreases the total time of operations because a response is not needed for the prior request before a subsequent request is made. This time we'll use a similar approach as before, except we will build a list of page URLs that can be used in asynchronous requests to populate our list of asset URLs more quickly.

First we define a new function `get_cmr_pages_urls()` to create a list of results pages URLs, not just the page numbers like we did before, then build that list.


In [ ]:
def get_cmr_pages_urls(collections, datetime_range, page_size): 
    response = requests.get(url,
                       params={
                           'concept_id': collections,
                           'temporal': datetime_range,
                           'page_size': page_size,
                       },
                       headers={
                           'Accept': 'application/json'
                       }
                      )
    hits = int(response.headers['CMR-Hits'])
    n_pages = math.ceil(hits/page_size)
    cmr_pages_urls = [f'{response.url}&page_num={x}'.replace('granules?', 'granules.json?') for x in list(range(1,n_pages+1))]
    return cmr_pages_urls

In [ ]:
urls = get_cmr_pages_urls(collections, datetime_range, page_size)
urls

Next, we create an empty list to populate with our asset URLs.

In [ ]:
results = []

Then we define a function `get_tasks()` to build a list of tasks for each page number URL and a function `get_url()` to make the requests for each page in parallel with one another.

In [ ]:
def get_tasks(session):
    tasks = []
    for l in urls:
        tasks.append(session.get(l))
    return tasks

In [ ]:
async def get_url():
    # Set a longer timeout (e.g., 10 minutes)
    timeout = aiohttp.ClientTimeout(total=600)
    async with aiohttp.ClientSession(timeout=timeout) as session:
        tasks = get_tasks(session)
        responses = await asyncio.gather(*tasks)
        for response in responses:
            if response.status == 200:
                res = await response.json()
                results.extend([l['href'] for g in res['feed']['entry'] for l in g['links'] if 'https' in l['href'] and '.hdf' in l['href']])
            else:
                print(f"Error: Received status {response.status} for {response.url}")


Run the functions to submit asynchronous/parallel requests for each page of results.

In [ ]:
start = time.time() 

await get_url()

end = time.time()

total_time = end - start
total_time

Much faster than before! We can see the same quantity of results and that a subsample of the resulting asset URLs matches what we retrieved before.

In [ ]:
len(results)

In [ ]:
data_urls[2025:2125] == results[2025:2125]

In [ ]:
async def fetch_page(session, url, collections, datetime_range, page_size, page_num):
    """
    Asynchronously fetches a single page of data and extracts granule URLs.
    
    Args:
        session (aiohttp.ClientSession): The aiohttp session to use for the request.
        url (str): The base URL for the API endpoint.
        collections (str): The concept ID for the collection.
        datetime_range (str): The temporal range for the data.
        page_size (int): The number of results per page.
        page_num (int): The page number to fetch.
        
    Returns:
        list: A list of data URLs (.hdf) found on the page, or an empty list if an error occurs.
    """
    params = {
        'concept_id': collections,
        'temporal': datetime_range,
        'page_size': page_size,
        'page_num': page_num
    }
    headers = {
        'Accept': 'application/json'
    }
    
    print(f"Requesting Page: {page_num}")
    try:
        # The 'async with' statement makes sure the request is non-blocking
        async with session.get(url, params=params, headers=headers) as response:
            # Raise an exception for bad status codes (4xx or 5xx)
            response.raise_for_status()
            print(f"Page {page_num} Response Code: {response.status}")
            
            # The 'await' keyword pauses the function until the JSON data is received
            data = await response.json()
            
            granules = data.get('feed', {}).get('entry', [])
            print(f"Page {page_num}: Found {len(granules)} Granules")
            
            page_data_urls = []
            for g in granules:
                # Extract links that contain 'https' and end with '.hdf'
                page_data_urls.extend([
                    x['href'] for x in g.get('links', []) 
                    if 'https' in x.get('href', '') and x.get('href', '').endswith('.hdf')
                ])
            return page_data_urls
            
    except aiohttp.ClientError as e:
        print(f"Error fetching page {page_num}: {e}")
        return [] # Return an empty list on error

async def main():
    """
    Main asynchronous function to orchestrate the fetching of all pages.
    """
    # --- Configuration (replace with your actual values) ---
    CMR_OPS = 'https://cmr.earthdata.nasa.gov/search' # CMR API Endpoint
    url = f'{CMR_OPS}/{"granules"}'
    
    collections = ['C1748058432-LPCLOUD'] # Collection or concept_id specific to LPDAAC Products (HLS Landsat OLI and HLS Sentinel-2 respectively) 
    datetime_range = '2000-02-24T00:00:00Z,2025-07-08T00:00:00Z'
    page_size = 2000
    
    # --- Execution ---
    start_time = time.time()
    all_data_urls = []
    
    # Use a single session for all requests for efficiency
    async with aiohttp.ClientSession() as session:
        
        # 1. Make an initial request to get the total number of hits
        print("--- Determining total number of pages ---")
        initial_params = {
            'concept_id': collections,
            'temporal': datetime_range,
            'page_size': 1 # We only need the headers, so request a small page size
        }
        async with session.get(url, params=initial_params) as response:
            response.raise_for_status()
            hits = int(response.headers.get('CMR-Hits', 0))
            if hits == 0:
                print("No granules found for the given criteria.")
                return

            n_pages = math.ceil(hits / page_size)
            print(f"Found {hits} total granules across {n_pages} pages.")

        # 2. Create and run tasks for all pages concurrently
        print("\n--- Fetching all pages concurrently ---")
        page_numbers = range(1, n_pages + 1)
        tasks = [
            fetch_page(session, url, collections, datetime_range, page_size, n)
            for n in page_numbers
        ]
        
        # asyncio.gather runs all tasks concurrently and collects their results
        results_from_pages = await asyncio.gather(*tasks)

        # 3. Flatten the list of lists into a single list of URLs
        all_data_urls = [url for sublist in results_from_pages for url in sublist]

        return all_data_urls
    
    end_time = time.time()
    
    print("\n--- Summary ---")
    print(f"Total Granule URLs found: {len(all_data_urls)}")
    print(f"Total time taken: {end_time - start_time:.2f} seconds")

In [ ]:
all_data_urls = await main()

In [ ]:
print(all_data_urls[0:2])

In [ ]:
earthaccess.download(all_data_urls[0], local_path='.',)

In [1]:
# analyse .hdf file to check if correct files are downloaded
import rioxarray
import matplotlib.pyplot as plt
import numpy as np

# define the path to the downloaded file
hdf_file = "/Users/lshms102/Documents/MPCP_lassa_sentinel/MOD11A1.A2000055.h12v10.061.2020043121102.hdf"

try:
    data_layer_str = f'HDF4_EOS:EOS_GRID:"{hdf_file}":MODIS_Grid_Daily_1km_LST:LST_Day_1km'

    # Open the specific subdataset using rioxarray
    rds = rioxarray.open_rasterio(data_layer_str)

except Exception as e:
    print(f"Error opening file: {e}")
    print("\nPlease ensure the HDF file is in the same directory as the script or provide the full path.")
    print("Also, ensure you have the necessary GDAL drivers, which are installed with rioxarray.")
    exit()

# The data is loaded as an xarray.DataArray. Let's inspect it.
print("--- DataArray Structure ---")
print(rds)
print("\n--- Coordinate Reference System (CRS) ---")
print(rds.rio.crs)



--- DataArray Structure ---
<xarray.DataArray (band: 1, y: 1200, x: 1200)> Size: 3MB
[1440000 values with dtype=uint16]
Coordinates:
  * band         (band) int64 8B 1
  * x            (x) float64 10kB -6.671e+06 -6.67e+06 ... -5.561e+06 -5.56e+06
  * y            (y) float64 10kB -1.112e+06 -1.113e+06 ... -2.223e+06
    spatial_ref  int64 8B 0
Attributes: (12/85)
    add_offset_err:                     0
    ALGORITHMPACKAGEACCEPTANCEDATE:     102004
    ALGORITHMPACKAGEMATURITYCODE:       Normal
    ALGORITHMPACKAGENAME:               MOD_PR11A
    ALGORITHMPACKAGEVERSION:            6
    ASSOCIATEDINSTRUMENTSHORTNAME.1:    MODIS
    ...                                 ...
    valid_range:                        7500, 65535
    VERSIONID:                          61
    VERTICALTILENUMBER:                 10
    WESTBOUNDINGCOORDINATE:             -63.855103293672
    _FillValue:                         0
    add_offset:                         0.0

--- Coordinate Reference System (